In [2]:
%matplotlib inline
import torch.nn as nn
import torch.nn.functional as F
import matplotlib.pyplot as plt
import numpy as np
import os
from scipy.ndimage import imread
from scipy import signal
import librosa as lbr
import IPython.display as ipd
import time
from collections import namedtuple
import pprint
from random import shuffle


import argparse
import itertools

import torchvision.transforms as transforms
from torch.utils.data import DataLoader
from torch.autograd import Variable
from PIL import Image
import torch


# from utils import ReplayBuffer
# from utils import LambdaLR
# from utils import Logger
# from utils import weights_init_normal
# from datasets import ImageDataset

In [ ]:
os.chdir("/Users/hongbozhu/Desktop/6104 project/genres/blues")

In [ ]:
def read_data(genre_A, genre_B, base_path="/Users/hongbozhu/Desktop/6104 project/genres/"):
    start_time=time.time()
    genre_A_path=base_path+str(genre_A)
    genre_B_path=base_path+str(genre_B)
    genre_A_song_path=os.listdir(genre_A_path)
    genre_A_song_path=[genre_A_path+"/"+i for i in genre_A_song_path]
    genre_B_song_path=os.listdir(genre_B_path)
    genre_B_song_path=[genre_B_path+"/"+i for i in genre_B_song_path]
    
#     def stft_transfer(song_path):
#         song, sr = lbr.load(song_path,sr=None)
#         f,t,song=signal.stft(song,fs=22050,nfft=512,nperseg=512)
#         song=np.log(song)
#         return song
    def matrix_song(song_path):
        song,sr=lbr.load(song_path,sr=None)
        song=np.asarray(song[:-32594])
        return song.reshape([-1,220,220])
    genre_A=list(map(matrix_song,genre_A_song_path[0:2]))
    genre_B=list(map(matrix_song,genre_B_song_path[0:2]))
    print("time spend is: ", time.time()-start_time)
    return genre_A, genre_B

genre_a,genre_b=read_data("blues","classical")



In [ ]:

A=[ image for song in genre_a for image in song ]
B=[ image for song in genre_b for image in song ]
train_A= np.asarray(A[0:13]).reshape([13,1,220,220])
test_A=np.asarray(A[13:]).reshape([13,1,220,220])
train_B=np.asarray(B[0:13]).reshape([13,1,220,220])
test_B=np.asarray(B[13:]).reshape([13,1,220,220])

#A=np.asarray(A)
#A=np.concatenate(A[:10],1)
l=train_B[0].reshape([-1])
# kk=np.exp(gen_B_temp_out.reshape([257,258]))
#b,q=signal.istft(kk, fs=22050,nfft=512,nperseg=512)
ipd.Audio(l,rate=22050)

In [211]:
#============================================== eidted

class ResidualBlock(nn.Module):
    def __init__(self, in_c):
        super(ResidualBlock, self).__init__()
        conv_block = [  nn.ReflectionPad2d(1),
                        nn.Conv2d(in_c, in_c, 3),
                        nn.InstanceNorm2d(in_c),
                        nn.ReLU(inplace=True),
                        nn.ReflectionPad2d(1),
                        nn.Conv2d(in_c, in_c, 3),
                        nn.InstanceNorm2d(in_c)  ]

        self.conv_block = nn.Sequential(*conv_block)
        
    def forward(self, x):
        return x + self.conv_block(x)
#===================================================
    

class Generator(nn.Module):
    def __init__(self, input_nc, output_nc, n_residual_blocks=9):
        super(Generator, self).__init__()
        
        start_kernels=20
        # Initial convolution block       
        model = [   nn.ReflectionPad2d(1),
                    nn.Conv2d(input_nc, start_kernels, 3),
                    nn.InstanceNorm2d(start_kernels),
                    nn.ReLU(inplace=True) ]

        # Downsampling
        in_features = start_kernels
        out_features = in_features*2
        for _ in range(2):    #[1,32,110,110]->[1,64,55,55]
            model += [  nn.Conv2d(in_features, out_features, 3, stride=2, padding=1),
                        nn.InstanceNorm2d(out_features),
                        nn.ReLU(inplace=True) ]
            in_features = out_features
            out_features = in_features*2

        # Residual blocks
        for _ in range(n_residual_blocks):
            model += [ResidualBlock(in_features)]

        # Upsampling
        out_features = in_features//2
        for _ in range(2):
            model += [  nn.ConvTranspose2d(in_features, out_features, 3, stride=2, padding=1, output_padding=1),
                        nn.InstanceNorm2d(out_features),
                        nn.ReLU(inplace=True) ]
            in_features = out_features
            out_features = in_features//2

        # Output layer
        model += [  nn.ReflectionPad2d(1),
                    nn.Conv2d(in_features, output_nc, 3),
                    nn.Tanh() ]

        self.model = nn.Sequential(*model)

    def forward(self, x):
        return self.model(x)

In [181]:
class Discriminator(nn.Module):
    def __init__(self, input_nc):
        super(Discriminator, self).__init__()
        start_feature=10
        # A bunch of convolutions one after another
        model = [   nn.Conv2d(input_nc, start_feature, 4, stride=2, padding=1), #[1,10,110,110]
                    nn.LeakyReLU(0.2, inplace=True) ]

        model += [  nn.Conv2d(start_feature,start_feature*2 , 4, stride=2, padding=1),   #[1,20,55,55]
                    nn.InstanceNorm2d(start_feature*2),
                    nn.LeakyReLU(0.2, inplace=True) ]

        model += [  nn.Conv2d(start_feature*2, start_feature*4, 4, stride=2, padding=1),  #[1,40,27,27]
                    nn.InstanceNorm2d(start_feature*4), 
                    nn.LeakyReLU(0.2, inplace=True) ]

        model += [  nn.Conv2d(start_feature*4, start_feature*8, 4,stride=2, padding=1),  #[1,80,13,13]
                    nn.InstanceNorm2d(start_feature*8), 
                    nn.LeakyReLU(0.2, inplace=True) ]

        # FCN classification layer
        model += [nn.Conv2d(start_feature*8, 1, 13,padding=0)] #[1,1,1,1]
        model+=[nn.Sigmoid()]
        self.model = nn.Sequential(*model)

    def forward(self, x):
        x =  self.model(x)
#         print(x.shape)
        # Average pooling and flatten
        return x

In [190]:
b=g(torch.Tensor(train_A[0:1]))
c=b.detach().numpy()
c=c.reshape([-1])
ipd.Audio(c,rate=22050)

In [204]:
d=Discriminator(1)
g=Generator(1,1)
opt_g=torch.optim.Adam(g.parameters(), lr=0.00002, betas=(0.5, 0.999))
opt_d=torch.optim.Adam(d.parameters(), lr=0.00002, betas=(0.5, 0.999))
l1=torch.nn.L1Loss()
for epoch in range(200):
    for i in range(len(train_A)):
        a=torch.Tensor(train_A[i:i+1])
        b=torch.Tensor(train_B[i:i+1])
        g.zero_grad()
        fakeB=g(a)
        los_b=torch.mean(torch.abs(fakeB-b))
        loss_g=Variable( d(fakeB),requires_grad=True)
        loss_g.backward()
        opt_g.step()
        if i %10==0:  
            loss_gan=torch.log(d(b))+torch.log((1-d(fakeB)))
            d.zero_grad()
            loss_gan.backward()
            opt_d.step()
        print("epoch: ", epoch, "batch: ",los_b, loss_g.item(), loss_gan.item())

epoch:  0 batch:  tensor(0.2484) 0.414364218711853 -1.3559393882751465
epoch:  0 batch:  tensor(0.2587) 0.49781885743141174 -1.3559393882751465
epoch:  0 batch:  tensor(0.2566) 0.46738606691360474 -1.3559393882751465
epoch:  0 batch:  tensor(0.2514) 0.4435327649116516 -1.3559393882751465
epoch:  0 batch:  tensor(0.2557) 0.5510825514793396 -1.3559393882751465
epoch:  0 batch:  tensor(0.2541) 0.5240611433982849 -1.3559393882751465
epoch:  0 batch:  tensor(0.2473) 0.40762951970100403 -1.3559393882751465
epoch:  0 batch:  tensor(0.2596) 0.5423662066459656 -1.3559393882751465
epoch:  0 batch:  tensor(0.2566) 0.5671373009681702 -1.3559393882751465
epoch:  0 batch:  tensor(0.2575) 0.5853869915008545 -1.3559393882751465
epoch:  0 batch:  tensor(0.2474) 0.597974956035614 -1.5326547622680664
epoch:  0 batch:  tensor(0.2448) 0.36657145619392395 -1.5326547622680664
epoch:  0 batch:  tensor(0.2552) 0.42487311363220215 -1.5326547622680664
epoch:  1 batch:  tensor(0.2484) 0.4601703882217407 -1.587793

epoch:  8 batch:  tensor(0.2448) 0.35351017117500305 -3.8790249824523926
epoch:  8 batch:  tensor(0.2552) 0.4223909080028534 -3.8790249824523926
epoch:  9 batch:  tensor(0.2484) 0.7782875895500183 -3.9109649658203125
epoch:  9 batch:  tensor(0.2587) 0.4783664345741272 -3.9109649658203125
epoch:  9 batch:  tensor(0.2566) 0.46570131182670593 -3.9109649658203125
epoch:  9 batch:  tensor(0.2514) 0.4331623911857605 -3.9109649658203125
epoch:  9 batch:  tensor(0.2557) 0.5425070524215698 -3.9109649658203125
epoch:  9 batch:  tensor(0.2541) 0.5160341858863831 -3.9109649658203125
epoch:  9 batch:  tensor(0.2473) 0.4029608368873596 -3.9109649658203125
epoch:  9 batch:  tensor(0.2596) 0.5542745590209961 -3.9109649658203125
epoch:  9 batch:  tensor(0.2566) 0.5699746608734131 -3.9109649658203125
epoch:  9 batch:  tensor(0.2575) 0.5725857019424438 -3.9109649658203125
epoch:  9 batch:  tensor(0.2474) 0.9062424898147583 -4.265974998474121
epoch:  9 batch:  tensor(0.2448) 0.3516277074813843 -4.26597499

KeyboardInterrupt: 

In [ ]:
b=g(torch.Tensor(train_A[0:1]))
c=b.detach().numpy()
c=c.reshape([-1])
ipd.Audio(c,rate=22050)

In [59]:
# parser = argparse.ArgumentParser()
# parser.add_argument('--epoch', type=int, default=0, help='starting epoch')
# parser.add_argument('--n_epochs', type=int, default=200, help='number of epochs of training')
# parser.add_argument('--batchSize', type=int, default=1, help='size of the batches')
# parser.add_argument('--dataroot', type=str, default=100,'datasets/horse2zebra/', help='root directory of the dataset')
# parser.add_argument('--lr', type=float, default=0.0002, help='initial learning rate')
# parser.add_argument('--decay_epoch', type=int, default=100, help='epoch to start linearly decaying the learning rate to 0')
# parser.add_argument('--size', type=int, default=256, help='size of the data crop (squared assumed)')
# parser.add_argument('--input_nc', type=int, default=3, help='number of channels of input data')
# parser.add_argument('--output_nc', type=int, default=3, help='number of channels of output data')
# parser.add_argument('--cuda', action='store_true', help='use GPU computation')
# parser.add_argument('--n_cpu', type=int, default=8, help='number of cpu threads to use during batch generation')
# opt = parser.parse_args()
# print(opt)
# if torch.cuda.is_available() and not opt.cuda:
#     print("WARNING: You have a CUDA device, so you should probably run with --cuda")


netG_A2B = Generator(1, 1)
netG_B2A = Generator(1, 1)
netD_A = Discriminator(1)
netD_B = Discriminator(1)

# if opt.cuda:
#     netG_A2B.cuda()
#     netG_B2A.cuda()
#     netD_A.cuda()
#     netD_B.cuda()

netG_A2B.apply(weights_init_normal)
netG_B2A.apply(weights_init_normal)
netD_A.apply(weights_init_normal)
netD_B.apply(weights_init_normal)

#Lossess
criterion_GAN = torch.nn.MSELoss()
criterion_cycle = torch.nn.L1Loss()
criterion_identity = torch.nn.L1Loss()

#Optimizers & LR schedulers
optimizer_G = torch.optim.Adam(itertools.chain(netG_A2B.parameters(), netG_B2A.parameters()),
                                lr=opt.lr, betas=(0.5, 0.999))
optimizer_D_A = torch.optim.Adam(netD_A.parameters(), lr=0.00002, betas=(0.5, 0.999))
optimizer_D_B = torch.optim.Adam(netD_B.parameters(), lr=0.00002, betas=(0.5, 0.999))

lr_scheduler_G = torch.optim.lr_scheduler.LambdaLR(optimizer_G, lr_lambda=LambdaLR(opt.n_epochs, opt.epoch, opt.decay_epoch).step)
lr_scheduler_D_A = torch.optim.lr_scheduler.LambdaLR(optimizer_D_A, lr_lambda=LambdaLR(opt.n_epochs, opt.epoch, opt.decay_epoch).step)
lr_scheduler_D_B = torch.optim.lr_scheduler.LambdaLR(optimizer_D_B, lr_lambda=LambdaLR(opt.n_epochs, opt.epoch, opt.decay_epoch).step)
netG_A2B = Generator(1, 1)
netG_A2B.apply(weights_init_normal)
loss_g_B = torch.nn.L1Loss()

optimizer_A2B = torch.optim.Adam(netG_A2B.parameters(), lr=0.0002, betas=(0.5, 0.999))
lr_scheduler_A2B = torch.optim.lr_scheduler.LambdaLR(optimizer_A2B, lr_lambda=LambdaLR(200, 0, 50).step)



usage: ipykernel_launcher.py [-h] [--epoch EPOCH] [--n_epochs N_EPOCHS]
                             [--batchSize BATCHSIZE] [--dataroot DATAROOT]
                             [--lr LR] [--decay_epoch DECAY_EPOCH]
                             [--size SIZE] [--input_nc INPUT_NC]
                             [--output_nc OUTPUT_NC] [--cuda] [--n_cpu N_CPU]
ipykernel_launcher.py: error: unrecognized arguments: -f /Users/hongbozhu/Library/Jupyter/runtime/kernel-fd5eee56-2519-4e38-a7d5-1a4558acc64c.json


SystemExit: 2

/Users/hongbozhu/anaconda3/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2918: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)


In [69]:
netG_A2B = Generator(1, 1)
netG_B2A = Generator(1, 1)
netD_A = Discriminator(1)
netD_B = Discriminator(1)


netG_A2B.apply(weights_init_normal)
netG_B2A.apply(weights_init_normal)
netD_A.apply(weights_init_normal)
netD_B.apply(weights_init_normal)

#Lossess
criterion_GAN = torch.nn.MSELoss()
criterion_cycle = torch.nn.L1Loss()
criterion_identity = torch.nn.L1Loss()

#Optimizers & LR schedulers
optimizer_G = torch.optim.Adam(itertools.chain(netG_A2B.parameters(), netG_B2A.parameters()),
                                lr=opt.lr, betas=(0.5, 0.999))
optimizer_D_A = torch.optim.Adam(netD_A.parameters(), lr=0.00002, betas=(0.5, 0.999))
optimizer_D_B = torch.optim.Adam(netD_B.parameters(), lr=0.00002, betas=(0.5, 0.999))

lr_scheduler_G = torch.optim.lr_scheduler.LambdaLR(optimizer_G, lr_lambda=LambdaLR(opt.n_epochs, opt.epoch, opt.decay_epoch).step)
lr_scheduler_D_A = torch.optim.lr_scheduler.LambdaLR(optimizer_D_A, lr_lambda=LambdaLR(opt.n_epochs, opt.epoch, opt.decay_epoch).step)
lr_scheduler_D_B = torch.optim.lr_scheduler.LambdaLR(optimizer_D_B, lr_lambda=LambdaLR(opt.n_epochs, opt.epoch, opt.decay_epoch).step)
# dataLoaderA=DataLoader()

0 0
1 1
2 2
3 3
4 4
5 5
6 6
7 7
8 8
9 9


In [ ]:
# A2B=======================================
netG_A2B = Generator(1, 1)
netG_A2B.apply(weights_init_normal)
loss_g_B = torch.nn.L1Loss()

optimizer_A2B = torch.optim.Adam(netG_A2B.parameters(), lr=0.0002, betas=(0.5, 0.999))
lr_scheduler_A2B = torch.optim.lr_scheduler.LambdaLR(optimizer_A2B, lr_lambda=LambdaLR(200, 0, 30).step)

for epoch in range(200):
    
    for i in range(len(train_A)):
        
        real_B = torch.Tensor(train_B[i:i+1])
        real_A=torch.Tensor(train_A[i:i+1])
        
        
    # A2B============================
        optimizer_A2B.zero_grad()

        fake_B=netG_A2B(real_B)

        loss = loss_g_B(fake_B, real_B)
        print("epoch: ",epoch,"batch: ",i, "loss: ", loss.item())

        loss.backward()
        optimizer_A2B.step()
    #D_B ===============================
    lr_scheduler_A2B.step()         
  

/Users/hongbozhu/Desktop/6104 project/PyTorch-CycleGAN-master/utils.py:114: UserWarning: nn.init.normal is now deprecated in favor of nn.init.normal_.
  torch.nn.init.normal(m.weight.data, 0.0, 0.02)


epoch:  0 batch:  0 loss:  0.14499491453170776
epoch:  0 batch:  1 loss:  0.11746960133314133
epoch:  0 batch:  2 loss:  0.11216510087251663
epoch:  0 batch:  3 loss:  0.09287656843662262
epoch:  0 batch:  4 loss:  0.06110289692878723
epoch:  0 batch:  5 loss:  0.056507375091314316
epoch:  0 batch:  6 loss:  0.045020099729299545
epoch:  0 batch:  7 loss:  0.0421956330537796
epoch:  0 batch:  8 loss:  0.02368154563009739
epoch:  0 batch:  9 loss:  0.02986798994243145
epoch:  0 batch:  10 loss:  0.028075097128748894
epoch:  0 batch:  11 loss:  0.02432934194803238
epoch:  0 batch:  12 loss:  0.028114333748817444
epoch:  1 batch:  0 loss:  0.04080608859658241
epoch:  1 batch:  1 loss:  0.049003966152668
epoch:  1 batch:  2 loss:  0.032417330890893936
epoch:  1 batch:  3 loss:  0.042499177157878876
epoch:  1 batch:  4 loss:  0.03184577450156212
epoch:  1 batch:  5 loss:  0.02432837150990963
epoch:  1 batch:  6 loss:  0.02779562771320343
epoch:  1 batch:  7 loss:  0.033139050006866455
epoch:

epoch:  13 batch:  2 loss:  0.01367006916552782
epoch:  13 batch:  3 loss:  0.016828572377562523
epoch:  13 batch:  4 loss:  0.010517513379454613
epoch:  13 batch:  5 loss:  0.00960233248770237
epoch:  13 batch:  6 loss:  0.01032906211912632
epoch:  13 batch:  7 loss:  0.012062741443514824
epoch:  13 batch:  8 loss:  0.013321100734174252
epoch:  13 batch:  9 loss:  0.011769202537834644
epoch:  13 batch:  10 loss:  0.008576156571507454
epoch:  13 batch:  11 loss:  0.008189363405108452
epoch:  13 batch:  12 loss:  0.010876255109906197
epoch:  14 batch:  0 loss:  0.017871972173452377
epoch:  14 batch:  1 loss:  0.03312036767601967
epoch:  14 batch:  2 loss:  0.013802379369735718
epoch:  14 batch:  3 loss:  0.017183003947138786
epoch:  14 batch:  4 loss:  0.011136127635836601
epoch:  14 batch:  5 loss:  0.009407573379576206
epoch:  14 batch:  6 loss:  0.011403472162783146
epoch:  14 batch:  7 loss:  0.012346056289970875
epoch:  14 batch:  8 loss:  0.01257315557450056
epoch:  14 batch:  9 l

epoch:  26 batch:  1 loss:  0.02707112766802311
epoch:  26 batch:  2 loss:  0.010850764811038971
epoch:  26 batch:  3 loss:  0.012587083503603935
epoch:  26 batch:  4 loss:  0.010341443121433258
epoch:  26 batch:  5 loss:  0.006141685880720615
epoch:  26 batch:  6 loss:  0.008883874863386154
epoch:  26 batch:  7 loss:  0.009802163578569889
epoch:  26 batch:  8 loss:  0.011775529012084007
epoch:  26 batch:  9 loss:  0.010839097201824188
epoch:  26 batch:  10 loss:  0.007265664637088776
epoch:  26 batch:  11 loss:  0.006708407308906317
epoch:  26 batch:  12 loss:  0.008393379859626293
epoch:  27 batch:  0 loss:  0.01394068356603384
epoch:  27 batch:  1 loss:  0.02605476602911949
epoch:  27 batch:  2 loss:  0.010722012259066105
epoch:  27 batch:  3 loss:  0.012261285446584225
epoch:  27 batch:  4 loss:  0.009148508310317993
epoch:  27 batch:  5 loss:  0.0063825370743870735
epoch:  27 batch:  6 loss:  0.008981563150882721
epoch:  27 batch:  7 loss:  0.009410886093974113
epoch:  27 batch:  

epoch:  38 batch:  12 loss:  0.006725078448653221
epoch:  39 batch:  0 loss:  0.011299066245555878
epoch:  39 batch:  1 loss:  0.018040897324681282
epoch:  39 batch:  2 loss:  0.011337355710566044
epoch:  39 batch:  3 loss:  0.01098424568772316
epoch:  39 batch:  4 loss:  0.008236640132963657
epoch:  39 batch:  5 loss:  0.0058540771715343
epoch:  39 batch:  6 loss:  0.007825036533176899
epoch:  39 batch:  7 loss:  0.009047589264810085
epoch:  39 batch:  8 loss:  0.008024517446756363
epoch:  39 batch:  9 loss:  0.006510762497782707
epoch:  39 batch:  10 loss:  0.0064845094457268715
epoch:  39 batch:  11 loss:  0.006320992950350046
epoch:  39 batch:  12 loss:  0.0072666676715016365
epoch:  40 batch:  0 loss:  0.014441315084695816
epoch:  40 batch:  1 loss:  0.017401287332177162
epoch:  40 batch:  2 loss:  0.010993755422532558
epoch:  40 batch:  3 loss:  0.01324501819908619
epoch:  40 batch:  4 loss:  0.009643647819757462
epoch:  40 batch:  5 loss:  0.006657610647380352
epoch:  40 batch: 

...

epoch:  103 batch:  1 loss:  0.005907486192882061
epoch:  103 batch:  2 loss:  0.0055714258924126625
epoch:  103 batch:  3 loss:  0.006177963223308325
epoch:  103 batch:  4 loss:  0.004501972813159227
epoch:  103 batch:  5 loss:  0.00360285397619009
epoch:  103 batch:  6 loss:  0.0046157753095030785
epoch:  103 batch:  7 loss:  0.004407872445881367
epoch:  103 batch:  8 loss:  0.0038614978548139334
epoch:  103 batch:  9 loss:  0.0038287541829049587
epoch:  103 batch:  10 loss:  0.0038071167655289173
epoch:  103 batch:  11 loss:  0.0036483847070485353
epoch:  103 batch:  12 loss:  0.0045878952369093895
epoch:  104 batch:  0 loss:  0.006813267711549997
epoch:  104 batch:  1 loss:  0.005724654998630285
epoch:  104 batch:  2 loss:  0.006318655796349049
epoch:  104 batch:  3 loss:  0.00637130718678236
epoch:  104 batch:  4 loss:  0.004670176655054092
epoch:  104 batch:  5 loss:  0.00366228842176497
epoch:  104 batch:  6 loss:  0.004289549309760332
epoch:  104 batch:  7 loss:  0.004612646996

epoch:  115 batch:  8 loss:  0.0034052159171551466
epoch:  115 batch:  9 loss:  0.0034144530072808266
epoch:  115 batch:  10 loss:  0.003470964962616563
epoch:  115 batch:  11 loss:  0.0035370667465031147
epoch:  115 batch:  12 loss:  0.0043586241081357
epoch:  116 batch:  0 loss:  0.006451956462115049
epoch:  116 batch:  1 loss:  0.005213396158069372
epoch:  116 batch:  2 loss:  0.005621917545795441
epoch:  116 batch:  3 loss:  0.005439301021397114
epoch:  116 batch:  4 loss:  0.004625636152923107
epoch:  116 batch:  5 loss:  0.003281561192125082
epoch:  116 batch:  6 loss:  0.003991470206528902
epoch:  116 batch:  7 loss:  0.00408886419609189
epoch:  116 batch:  8 loss:  0.0032272771932184696
epoch:  116 batch:  9 loss:  0.0033778955694288015
epoch:  116 batch:  10 loss:  0.00337757496163249
epoch:  116 batch:  11 loss:  0.0034174667671322823
epoch:  116 batch:  12 loss:  0.004271517973393202
epoch:  117 batch:  0 loss:  0.006264758296310902
epoch:  117 batch:  1 loss:  0.00551177281

epoch:  128 batch:  2 loss:  0.005750661250203848
epoch:  128 batch:  3 loss:  0.005589312873780727
epoch:  128 batch:  4 loss:  0.004436665214598179
epoch:  128 batch:  5 loss:  0.003426071023568511
epoch:  128 batch:  6 loss:  0.004019823390990496
epoch:  128 batch:  7 loss:  0.0042448220774531364
epoch:  128 batch:  8 loss:  0.003347522346302867
epoch:  128 batch:  9 loss:  0.0031079521868377924
epoch:  128 batch:  10 loss:  0.003527230117470026
epoch:  128 batch:  11 loss:  0.0032851877622306347
epoch:  128 batch:  12 loss:  0.004246847704052925
epoch:  129 batch:  0 loss:  0.006329075433313847
epoch:  129 batch:  1 loss:  0.005060688126832247
epoch:  129 batch:  2 loss:  0.0052502090111374855
epoch:  129 batch:  3 loss:  0.005548163782805204
epoch:  129 batch:  4 loss:  0.003961634822189808
epoch:  129 batch:  5 loss:  0.0036212417762726545
epoch:  129 batch:  6 loss:  0.0037932207342237234
epoch:  129 batch:  7 loss:  0.004607063252478838
epoch:  129 batch:  8 loss:  0.0031564233

epoch:  140 batch:  9 loss:  0.003285422222688794
epoch:  140 batch:  10 loss:  0.0031360916327685118
epoch:  140 batch:  11 loss:  0.003120535286143422
epoch:  140 batch:  12 loss:  0.004124105907976627
epoch:  141 batch:  0 loss:  0.005970040336251259
epoch:  141 batch:  1 loss:  0.004909933544695377
epoch:  141 batch:  2 loss:  0.0050954981707036495
epoch:  141 batch:  3 loss:  0.00546839227899909
epoch:  141 batch:  4 loss:  0.0038385812658816576
epoch:  141 batch:  5 loss:  0.0035870515275746584
epoch:  141 batch:  6 loss:  0.0041084010154008865
epoch:  141 batch:  7 loss:  0.003999070264399052
epoch:  141 batch:  8 loss:  0.0032898979261517525
epoch:  141 batch:  9 loss:  0.003286113031208515
epoch:  141 batch:  10 loss:  0.0032217209227383137
epoch:  141 batch:  11 loss:  0.003145969472825527
epoch:  141 batch:  12 loss:  0.004044921137392521
epoch:  142 batch:  0 loss:  0.005936271045356989
epoch:  142 batch:  1 loss:  0.004757199436426163
epoch:  142 batch:  2 loss:  0.0049931

epoch:  153 batch:  3 loss:  0.004831753205507994
epoch:  153 batch:  4 loss:  0.003299943171441555
epoch:  153 batch:  5 loss:  0.003300832351669669
epoch:  153 batch:  6 loss:  0.0036140670999884605
epoch:  153 batch:  7 loss:  0.0033241247292608023
epoch:  153 batch:  8 loss:  0.0027930191718041897
epoch:  153 batch:  9 loss:  0.0031112651340663433
epoch:  153 batch:  10 loss:  0.0029836143366992474
epoch:  153 batch:  11 loss:  0.0029742491897195578
epoch:  153 batch:  12 loss:  0.003925692290067673
epoch:  154 batch:  0 loss:  0.005684413015842438
epoch:  154 batch:  1 loss:  0.004258655942976475
epoch:  154 batch:  2 loss:  0.004538127686828375
epoch:  154 batch:  3 loss:  0.004674185998737812
epoch:  154 batch:  4 loss:  0.003230318194255233
epoch:  154 batch:  5 loss:  0.003138660453259945
epoch:  154 batch:  6 loss:  0.0035226528998464346
epoch:  154 batch:  7 loss:  0.003366227960214019
epoch:  154 batch:  8 loss:  0.0028273342177271843
epoch:  154 batch:  9 loss:  0.00319207

In [169]:
   
# # ######. net-work
netG_A2B = Generator(1, 1)
netG_B2A = Generator(1, 1)
netD_A = Discriminator(1)
netD_B = Discriminator(1)


netG_A2B.apply(weights_init_normal)
netG_B2A.apply(weights_init_normal)
netD_A.apply(weights_init_normal)
netD_B.apply(weights_init_normal)

#Lossess
criterion_GAN = torch.nn.MSELoss()
criterion_cycle = torch.nn.L1Loss()
criterion_identity = torch.nn.L1Loss()

#Optimizers & LR schedulers
optimizer_G = torch.optim.Adam(itertools.chain(netG_A2B.parameters(), netG_B2A.parameters()),
                                lr=0.00002, betas=(0.5, 0.999))
optimizer_D_A = torch.optim.Adam(netD_A.parameters(), lr=0.00002, betas=(0.5, 0.999))
optimizer_D_B = torch.optim.Adam(netD_B.parameters(), lr=0.00002, betas=(0.5, 0.999))

lr_scheduler_G = torch.optim.lr_scheduler.LambdaLR(optimizer_G, lr_lambda=LambdaLR(200, 0, 50).step)
lr_scheduler_D_A = torch.optim.lr_scheduler.LambdaLR(optimizer_D_A, lr_lambda=LambdaLR(200, 0, 50).step)
lr_scheduler_D_B = torch.optim.lr_scheduler.LambdaLR(optimizer_D_B, lr_lambda=LambdaLR(200, 0, 50).step)

# dataLoaderA=DataLoader()
for epoch in range(200):
    start_time=time.time()
    for i in range(len(train_A)):
        
        real_B = torch.Tensor(train_B[i:i+1])
        real_A=torch.Tensor(train_A[i:i+1])
        
        
        ###### Generators A2B and B2A ######
        optimizer_G.zero_grad()
        # Identity loss
        # G_A2B(B) should equal B if real B is fed
        same_B = netG_A2B(real_B)
        loss_identity_B = criterion_identity(same_B, real_B)*5.0
        # G_B2A(A) should equal A if real A is fed
        same_A = netG_B2A(real_A)
        loss_identity_A = criterion_identity(same_A, real_A)*5.0

        # GAN loss
        fake_B = netG_A2B(real_A)
        loss_GAN_A2B = nn.CrossEntropyLoss(netD_B(fake_B)

        fake_A = netG_B2A(real_B)
        loss_GAN_B2A = netD_A(fake_A)

        # Cycle loss
        recovered_A = netG_B2A(fake_B)
        loss_cycle_ABA = criterion_cycle(recovered_A, real_A)*10.0

        recovered_B = netG_A2B(fake_A)
        loss_cycle_BAB = criterion_cycle(recovered_B, real_B)*10.0

        # Total loss
        loss_G = loss_identity_A + loss_identity_B + loss_GAN_A2B + loss_GAN_B2A + loss_cycle_ABA + loss_cycle_BAB
        loss_G.backward()
        
        optimizer_G.step()
        ###################################

        ###### Discriminator A ######
        optimizer_D_A.zero_grad()

        # Real loss
        loss_D_realA =netD_A(real_A)
        

        # Fake loss
        loss_D_fakeA =netD_A(fake_A)

        # Total loss
        loss_D_A = (loss_D_realA + loss_D_fakeA)*0.5
        loss_D_A.backward(retain_graph=True)

        optimizer_D_A.step()
        ###################################

        ###### Discriminator B ######
        optimizer_D_B.zero_grad()

        # Real loss
        loss_D_realB =torch.log(netD_B(real_B))
        

        # Fake loss
        loss_D_fakeB = torch.log(1-netD_B(fake_B))

        # Total loss
        loss_D_B = (loss_D_realB + loss_D_fakeB)*0.5
        loss_D_B.backward()

        optimizer_D_B.step()
        
        ###################################
        now=time.time()
        dif=start_time-now
        print("time: ", dif ," epoch:", epoch, " batch:", i, " loss_G: ",loss_G, " loss_D_A: ", loss_D_A, " loss_D_B: ", loss_D_A)

    
    print("done")
    print(same_b.shape)
        

/Users/hongbozhu/Desktop/6104 project/PyTorch-CycleGAN-master/utils.py:114: UserWarning: nn.init.normal is now deprecated in favor of nn.init.normal_.
  torch.nn.init.normal(m.weight.data, 0.0, 0.02)


torch.Size([1, 1, 1, 1])
torch.Size([1, 1, 1, 1])
torch.Size([1, 1, 1, 1])
torch.Size([1, 1, 1, 1])


RuntimeError: Trying to backward through the graph a second time, but the buffers have already been freed. Specify retain_graph=True when calling backward the first time.

In [ ]:
b=netG_A2B(torch.Tensor(train_B))
c=b.detach().numpy()
c=c.reshape([-1])
ipd.Audio(c,rate=22050)
# l=train_A.reshape([-1])
# # kk=np.exp(gen_B_temp_out.reshape([257,258]))
# #b,q=signal.istft(kk, fs=22050,nfft=512,nperseg=512)
#ipd.Audio(l,rate=22050)


In [ ]:
A=[ image for song in genre_a for image in song ]
B=[ image for song in genre_b for image in song ]
train_A= np.asarray(A[0:13]).reshape([13,1,220,220])
test_A=np.asarray(A[13:]).reshape([13,1,220,220])
train_B=np.asarray(B[0:13]).reshape([13,1,220,220])
test_B=np.asarray(B[13:]).reshape([13,1,220,220])

#A=np.asarray(A)
#A=np.concatenate(A[:10],1)
l=train_B.reshape([-1])
# kk=np.exp(gen_B_temp_out.reshape([257,258]))
#b,q=signal.istft(kk, fs=22050,nfft=512,nperseg=512)
ipd.Audio(l,rate=22050)

In [ ]:
# Inputs & targets memory allocation
# Tensor = torch.cuda.FloatTensor if opt.cuda else torch.Tensor
# input_A = Tensor(opt.batchSize, opt.input_nc, opt.size, opt.size)
# input_B = Tensor(opt.batchSize, opt.output_nc, opt.size, opt.size)
# target_real = Variable(Tensor(opt.batchSize).fill_(1.0), requires_grad=False)
# target_fake = Variable(Tensor(opt.batchSize).fill_(0.0), requires_grad=False)

# fake_A_buffer = ReplayBuffer()
# fake_B_buffer = ReplayBuffer()

# Dataset loader
# transforms_ = [ transforms.Resize(int(opt.size*1.12), Image.BICUBIC), 
#                 transforms.RandomCrop(opt.size), 
#                 transforms.RandomHorizontalFlip(),
#                 transforms.ToTensor(),
#                 transforms.Normalize((0.5,0.5,0.5), (0.5,0.5,0.5)) ]
# dataloader = DataLoader(ImageDataset(opt.dataroot, transforms_=transforms_, unaligned=True), 
#                         batch_size=opt.batchSize, shuffle=True, num_workers=opt.n_cpu)

# Loss plot
# logger = Logger(opt.n_epochs, len(dataloader))
###################################



###### Training ######
for epoch in range(opt.epoch, opt.n_epochs):
    for i, batch in enumerate(dataloader):
        # Set model input
        real_A = Variable(input_A.copy_(batch['A']))
        real_B = Variable(input_B.copy_(batch['B']))

        ###### Generators A2B and B2A ######
        optimizer_G.zero_grad()

        # Identity loss
        # G_A2B(B) should equal B if real B is fed
        same_B = netG_A2B(real_B)
        loss_identity_B = criterion_identity(same_B, real_B)*5.0
        # G_B2A(A) should equal A if real A is fed
        same_A = netG_B2A(real_A)
        loss_identity_A = criterion_identity(same_A, real_A)*5.0

        # GAN loss
        fake_B = netG_A2B(real_A)
        pred_fake = netD_B(fake_B)
        loss_GAN_A2B = criterion_GAN(pred_fake, target_real)

        fake_A = netG_B2A(real_B)
        pred_fake = netD_A(fake_A)
        loss_GAN_B2A = criterion_GAN(pred_fake, target_real)

        # Cycle loss
        recovered_A = netG_B2A(fake_B)
        loss_cycle_ABA = criterion_cycle(recovered_A, real_A)*10.0

        recovered_B = netG_A2B(fake_A)
        loss_cycle_BAB = criterion_cycle(recovered_B, real_B)*10.0

        # Total loss
        loss_G = loss_identity_A + loss_identity_B + loss_GAN_A2B + loss_GAN_B2A + loss_cycle_ABA + loss_cycle_BAB
        loss_G.backward()
        
        optimizer_G.step()
        ###################################

        ###### Discriminator A ######
        optimizer_D_A.zero_grad()

        # Real loss
        pred_real = netD_A(real_A)
        loss_D_real = criterion_GAN(pred_real, target_real)

        # Fake loss
        fake_A = fake_A_buffer.push_and_pop(fake_A)
        pred_fake = netD_A(fake_A.detach())
        loss_D_fake = criterion_GAN(pred_fake, target_fake)

        # Total loss
        loss_D_A = (loss_D_real + loss_D_fake)*0.5
        loss_D_A.backward()

        optimizer_D_A.step()
        ###################################

        ###### Discriminator B ######
        optimizer_D_B.zero_grad()

        # Real loss
        pred_real = netD_B(real_B)
        loss_D_real = criterion_GAN(pred_real, target_real)
        
        # Fake loss
        fake_B = fake_B_buffer.push_and_pop(fake_B)
        pred_fake = netD_B(fake_B.detach())
        loss_D_fake = criterion_GAN(pred_fake, target_fake)

        # Total loss
        loss_D_B = (loss_D_real + loss_D_fake)*0.5
        loss_D_B.backward()

        optimizer_D_B.step()
        ###################################

        # Progress report (http://localhost:8097)
        logger.log({'loss_G': loss_G, 'loss_G_identity': (loss_identity_A + loss_identity_B), 'loss_G_GAN': (loss_GAN_A2B + loss_GAN_B2A),
                    'loss_G_cycle': (loss_cycle_ABA + loss_cycle_BAB), 'loss_D': (loss_D_A + loss_D_B)}, 
                    images={'real_A': real_A, 'real_B': real_B, 'fake_A': fake_A, 'fake_B': fake_B})

    # Update learning rates
    lr_scheduler_G.step()
    lr_scheduler_D_A.step()
    lr_scheduler_D_B.step()

    # Save models checkpoints
    torch.save(netG_A2B.state_dict(), 'output/netG_A2B.pth')
    torch.save(netG_B2A.state_dict(), 'output/netG_B2A.pth')
    torch.save(netD_A.state_dict(), 'output/netD_A.pth')
    torch.save(netD_B.state_dict(), 'output/netD_B.pth')
###################################



In [3]:
a,sr_a=lbr.load("/Users/hongbozhu/Desktop/6104 project/output/a.mp3",sr=None)
b,sr_b=lbr.load("/Users/hongbozhu/Desktop/6104 project/output/b.mp3",sr=None)
t_b,sr_tb=lbr.load("/Users/hongbozhu/Desktop/6104 project/output/t_b.mp3",sr=None)

In [4]:
print(len(a),len(b),len(t_b))

911250 911250 911250


In [5]:
a=a[len(a)//20*8:]
b=b[len(a)//20*8:]
t_b=t_b[len(a)//20*8:]

In [6]:

ipd.Audio(a,rate=sr_a)

In [7]:
ipd.Audio(b,rate=sr_b)

In [8]:
ipd.Audio(t_b,rate=sr_tb)

In [12]:
lbr.output.write_wav("/Users/hongbozhu/Desktop/6104 project/a.mp3",a,sr_a)

In [10]:
lbr.output.write_wav("/Users/hongbozhu/Desktop/6104 project/b.mp3",b,sr_b)

In [15]:
lbr.output.write_wav("/Users/hongbozhu/Desktop/6104 project/t_b.mp3",t_b,sr_tb)